# Anomaly Detection System Overview

This Notebook demonstrates a comprehensive approach to anomaly detection in operational data using various machine learning techniques. It encompasses data preprocessing, rule-based anomaly detection, univariate and multivariate anomaly detection methods, and visualizations to illustrate the detected anomalies.

## Contents
1. [Introduction](#Introduction)
2. [Data Preprocessing](#Data-Preprocessing)
3. [Rule-based Anomaly Detection](#Rule-based-Anomaly-Detection)
4. [Univariate Anomaly Detection](#Univariate-Anomaly-Detection)
5. [Multivariate Anomaly Detection](#Multivariate-Anomaly-Detection)
6. [Visualizing Anomalies](#Visualizing-Anomalies)
7. [Conclusion](#Conclusion)

## Introduction
This section provides an overview of the anomaly detection system, its objectives, and the significance of anomaly detection in operational data analysis.

## Data Preprocessing
The initial step involves cleaning the data, handling missing values, and preparing the data for analysis. We start with the necessary libraries.

In [2]:
import pandas as pd
import numpy as np
from sklearn.ensemble import IsolationForest
from sklearn.preprocessing import MinMaxScaler, StandardScaler
from sklearn.decomposition import PCA
from sklearn import preprocessing
from sklearn.cluster import KMeans
import matplotlib.pyplot as plt
import os
from sklearn.metrics import silhouette_score
from functools import reduce
import plotly.graph_objs as go
from plotly.subplots import make_subplots
import plotly.express as px

### Load data from a CSV file

This section demonstrates how to load a single CSV file containing operational data. The code snippet below reads the data from the specified file path, converts the timestamp column to datetime format according to the provided datetime format, and sets this column as the index of the DataFrame. This process is essential for preparing the data for time-series analysis and anomaly detection.


In [3]:
# Path to the CSV file
file_path = 'data.csv' 
# Timestamp column name and datetime format
timestamp_col = 'Timestamp' 
datetime_format = '%d.%m.%Y %H:%M' 

# Loading CSV file
df = pd.read_csv(file_path, encoding='latin1', sep=';', decimal=',')
# Convert timestamp column to datetime and set it as index
df[timestamp_col] = pd.to_datetime(df[timestamp_col], format=datetime_format)
df.set_index(timestamp_col, inplace=True)

# Checking the DataFrame
print(df.head())

<h2 align="center">Load Data from Database</h2>
 

### SQL Query and Required parameters for the data retrieval

In [ ]:
sql_query = """WITH AggregatedData AS (
  SELECT 
    SensorID, 
    MeasurementValue,
    RoundedTime = DATEADD(MINUTE, DATEDIFF(MINUTE, 0, MeasurementTime) / 5 * 5, 0)
  FROM 
    SensorMeasurements
  WHERE 
    SensorID IN (101, 102, 103, 104, 105, 106, 107, 108, 109)  -- Example sensor IDs
    AND MeasurementTime >= '2023-01-01T00:00:00'
    AND MeasurementTime <= '2023-01-31T23:59:59'
),
PivotedData AS (
  SELECT 
    RoundedTime,
    [101] AS OrganicLoad, 
    [102] AS OzoneLevel, 
    [103] AS InletQuality, 
    [104] AS OutletQuality, 
    [105] AS UVIntensity,
    [106] AS InletTurbidity,
    [107] AS OutletTurbidity,
    [108] AS InletPressure,
    [109] AS OutletPressure
  FROM 
    AggregatedData
  PIVOT (
    AVG(MeasurementValue) 
    FOR SensorID IN ([101], [102], [103], [104], [105], [106], [107], [108], [109])
  ) AS PivotTable
)
SELECT 
  RoundedTime,
  COALESCE(OrganicLoad, -100),
  COALESCE(OzoneLevel, -100),
  COALESCE(InletQuality, -100),
  COALESCE(OutletQuality, -100),
  COALESCE(UVIntensity, -100),
  COALESCE(InletTurbidity, -100),
  COALESCE(OutletTurbidity, -100),
  COALESCE(InletPressure, -100),
  COALESCE(OutletPressure, -100)'
FROM 
  PivotedData
ORDER BY 
  RoundedTime;
"""


server = 'YourDatabaseServer'  
database = 'YourDatabaseName' 
username = 'YourUsername'  
password = 'YourPassword'  
host = 'YourDatabaseServer'  
timestamp_col = "TimeBlock" 
datetime_format = "%Y-%m-%dT%H:%M:%S"  

conn_str = f'mssql+pyodbc://{username}:{password}@{host}/{database}?driver=ODBC+Driver+17+for+SQL+Server'


In [ ]:

from sqlalchemy import create_engine

def load_data_from_db(sql_query, conn_str, timestamp_col, datetime_format):
    """
    Reads data from a database using SQLAlchemy, converts the timestamp column to datetime,
    and returns a DataFrame.

    Args:
    sql_query (str): The SQL query to execute.
    conn_str (str): SQLAlchemy connection string for the database.
    timestamp_col (str): The name of the timestamp column.
    datetime_format (str): The datetime format of the timestamp column.

    Returns:
    pandas.DataFrame: DataFrame containing the processed data.
    """
    # Create a database connection engine
    engine = create_engine(conn_str)
    
    # Use the engine to execute the SQL query and fetch results as a DataFrame
    df = pd.read_sql_query(sql_query, engine)
    
    # Convert the timestamp column to datetime and set it as index
    if timestamp_col and datetime_format:
        df[timestamp_col] = pd.to_datetime(df[timestamp_col], format=datetime_format)
        df.set_index(timestamp_col, inplace=True)
    
    return df

In [ ]:


server = 'YourDatabaseServer'  # Veritabanı sunucusunun adı veya IP adresi
database = 'YourDatabaseName'  # Veritabanının adı
username = 'YourUsername'  # Veritabanı kullanıcı adı
password = 'YourPassword'  # Kullanıcının şifresi
host = 'YourDatabaseServer'  # Veritabanı sunucusunun adı veya IP adresi, tekrar girilebilir
timestamp_col = "TimeBlock"  # Verilerinize göre ayarlayın
datetime_format = "%Y-%m-%dT%H:%M:%S"  # Verilerinizin formatına göre ayarlayın

conn_str = f'mssql+pyodbc://{username}:{password}@{host}/{database}?driver=ODBC+Driver+17+for+SQL+Server'

from sqlalchemy import create_engine

def load_data_from_db(sql_query, conn_str, timestamp_col, datetime_format):
    """
    Reads data from a database using SQLAlchemy, converts the timestamp column to datetime,
    and returns a DataFrame.

    Args:
    sql_query (str): The SQL query to execute.
    conn_str (str): SQLAlchemy connection string for the database.
    timestamp_col (str): The name of the timestamp column.
    datetime_format (str): The datetime format of the timestamp column.

    Returns:
    pandas.DataFrame: DataFrame containing the processed data.
    """
    # Create a database connection engine
    engine = create_engine(conn_str)
    
    # Use the engine to execute the SQL query and fetch results as a DataFrame
    df = pd.read_sql_query(sql_query, engine)
    
    # Convert the timestamp column to datetime and set it as index
    if timestamp_col and datetime_format:
        df[timestamp_col] = pd.to_datetime(df[timestamp_col], format=datetime_format)
        df.set_index(timestamp_col, inplace=True)
    
    return df

### Handling Missing Values with Custom Markers

The `handle_missing_values` function is designed to effectively manage missing values in datasets obtained from databases, where `-100` is used as a custom marker to indicate missing measurements. This approach allows us to distinguish between actual missing values and those artificially marked due to the absence of data. By converting `-100` values to `NaN`, we can apply forward-fill to replace missing values with the previous non-missing value, ensuring the continuity of data without conflating genuinely missing data with placeholders. This method is especially useful in time-series datasets, where the temporal sequence is crucial, and it's essential to differentiate between missing values inherent to the dataset and those introduced during data processing. The function also removes columns or rows with missing values exceeding a defined threshold, preserving only those data points that offer real, actionable insights.



In [4]:
## Missing value Handlung
def handle_missing_values(df, threshold=0.5):
    """
    Handles missing values in a Pandas DataFrame by initially replacing custom marked missing values (-100)
    with NaN, to differentiate between actual missing values from the database and the ones marked intentionally.
    Then, drops columns or rows with a high proportion of missing values above a specified threshold and fills in
    the remaining missing values with the previous value in the same column using forward fill method. This approach
    ensures that real missing values are treated accordingly, and only significant columns with genuine data are retained.

    Args:
        df (pd.DataFrame): Pandas DataFrame containing the data with custom marked missing values.
        threshold (float): Fraction of missing values above which columns or rows will be dropped. Defaults to 0.5.

    Returns:
        pd.DataFrame: DataFrame with missing values handled, preserving the integrity of real missing data.
    """
       
    # Replace all non-numeric values with NaN       
    for col in df.columns:
        try:
            df[col] = df[col].astype(str).str.replace(',', '.')
            df[col] = df[col].replace({r'\s+': np.nan, '\xa0': np.nan}, regex=True)
            # Convert column to float
            df[col] = df[col].astype(float)
        except ValueError as e:
            print(f"Warning: Could not convert column {col} to float. Error: {e}")
   

    # Calculate the proportion of missing values for each column and row
    missing_ratio_col = df.isnull().mean()
    missing_ratio_row = df.isnull().mean(axis=1)

    # Drop columns with a high proportion of missing values
    columns_to_drop = missing_ratio_col[missing_ratio_col >= threshold].index
    df.drop(columns=columns_to_drop, inplace=True)

    # Drop rows with a high proportion of missing values
    rows_to_drop = missing_ratio_row[missing_ratio_row >= threshold].index
    df.drop(index=rows_to_drop, inplace=True)
   
    # Replace custom marked missing values (-100) with NaN to differentiate them from actual missing values      
    df.replace(-100, np.nan, inplace=True) 

    # Fill in the remaining missing values with the previous value in the same column
    df.ffill(inplace=True)

    # If there are still any missing values (e.g., at the start), fill with the next valid value
    df.bfill(inplace=True)

    return df


### Add Anomalies to a list

It is the necessary function to create a list of detected anomalies and save it in the database. 

In [5]:
def add_anomaly_details(anomalies_list, param, pvid, index, score, anomaly_type, additional_info=''):
    """
    Adds details of detected anomalies to a list.

    Args:
        anomalies_list (list): List where detected anomaly details will be appended.
        param (str): Name of the parameter in which the anomaly was detected.
        pvid (str): PVID associated with the parameter.
        index: Index or timestamp of the anomaly.
        score (float): Anomaly score.
        anomaly_type (str): Type of anomaly ('Rule-based', 'Univariate', 'Multivariate').
        additional_info (str): Additional information about the anomaly. Optional.
    """
    anomalies_list.append({
        'Parameter Name': param,
        'PVID': pvid,
        'Anomaly Type': anomaly_type,
        'Timestamp': index,
        'Anomaly Score': score,
        'Additional Info': additional_info
    })



<h2 align="center">Rule-based Anomaly Process</h2>

Rule-based anomaly detection is the process of identifying anomalies based on established rules or thresholds. This method is particularly useful when you have in-depth knowledge of a particular area and the boundaries between normal and abnormal are clearly defined. The normal operating ranges of each feature (column) in the data set are predetermined and values that fall outside these ranges are flagged as anomaly.

In [6]:
fallback_anomaly_criteria = {
    "OrganicLoad": (30, 60),  # Organic Matter Load
    "OzoneLevel": (30, 150),  # Gas Ozone Concentration
    "InletQuality": (15, 35),  # Inlet Water Quality
    "OutletQuality": (5, 20),  # Outlet Water Quality
    "UVIntensity": (25, 70),  # UV Light Intensity
    "InletTurbidity": (0, 2),  # Inlet Turbidity
    "OutletTurbidity": (0, 2),  # Outlet Turbidity
    "InletPressure": (0, 1500),  # Inlet Pressure
    "OutletPressure": (0, 1500),  # Outlet Pressure
}


### Reading Anomaly Criteria and PVID from Excel

The function `read_anomaly_criteria_and_pvid` is designed to facilitate the loading of external anomaly criteria and PVID (Process Variable Identifier) information, which are crucial for conducting rule-based anomaly detection. This function reads from an Excel file, which is expected to contain a list of variables along with their minimum and maximum threshold values for anomaly detection, and their corresponding PVIDs. This approach allows for easy updates and modifications of the anomaly detection criteria without altering the codebase, promoting flexibility and ease of maintenance.


In [155]:

def read_anomaly_criteria_and_pvid(file_path):
    """
    Reads anomaly criteria and PVID information from an Excel file.

    Args:
        file_path (str): Path to the Excel file containing anomaly criteria and PVIDs.

    Returns:
        dict: A dictionary containing anomaly criteria and PVIDs for each parameter.
    """
    df = pd.read_excel(file_path)
    criteria_and_pvid = {}
    for _, row in df.iterrows():
        variable = row['Variable']
        min_val = row['Min']
        max_val = row['Max']
        pvid = row['PVID']
        criteria_and_pvid[variable] = {'min': min_val, 'max': max_val, 'pvid': pvid}
    return criteria_and_pvid



### Rule-based Anomaly Detection

After acquiring the anomaly detection criteria and PVIDs through `read_anomaly_criteria_and_pvid`, the next step involves applying these criteria to identify anomalies within the dataset. The rule-based anomaly detection approach evaluates each data point against the predefined minimum and maximum thresholds. Data points falling outside of these thresholds are flagged as anomalies. This method is particularly effective for datasets where the normal operational ranges are well-defined and deviations from these ranges indicate potential issues or outliers.


In [156]:

def detect_rule_based_anomalies(df, criteria_and_pvid):
    """
    Detects rule-based anomalies based on predefined criteria and marks them in the DataFrame.
    
    Args:
        df (pd.DataFrame): DataFrame containing the data to be analyzed.
        criteria_and_pvid (dict): Dictionary containing the anomaly criteria and PVIDs for each parameter.
    
    Returns:
        pd.DataFrame: Updated DataFrame with a new column indicating rule-based anomalies.
        list: A list of dictionaries with details about each detected rule-based anomaly.
    """
    anomalies_list = []
    df['Anomaly_Rulebased'] = 0  # Initialize the column to mark rule-based anomalies

    for param, criteria in criteria_and_pvid.items():
        if param in df.columns:
            min_val, max_val = criteria['min'], criteria['max']
            is_anomaly = (df[param] < min_val) | (df[param] > max_val)
            df['Anomaly_Rulebased'] |= is_anomaly.astype(int)

            # Here we iterate over each anomaly and add details to the list
            for index, value in df[param][is_anomaly].items():
                # 'N/A' used for score as it is not applicable for rule-based anomalies
                add_anomaly_details(anomalies_list, param, criteria['pvid'], index, 'N/A', 'Rule-based', f'Value {value} is outside the range [{min_val}, {max_val}]')
    
    return df, anomalies_list


<h2 align = "center">Univariate Anomaly Detection</h2>

### Determine Contamination

The `determine_contamination` function calculates the contamination rate which is essential for setting the threshold in anomaly detection algorithms. This rate is determined based on the distribution of anomaly scores, identifying the proportion of data points considered as outliers. The function calculates the first (Q1) and third (Q3) quartiles of the scores, computes the Interquartile Range (IQR), and identifies scores beyond 1.5 times the IQR as outliers. The contamination rate is then set to ensure a minimum level of detected anomalies, with a cap to limit the rate and reduce false positives. This dynamic approach allows for adaptive thresholding based on the actual data distribution.


In [157]:
def determine_contamination(scores):
    """
    Defines the contamination factor for anomaly detection based on the distribution of anomaly scores.

    Args:
        scores (numpy.ndarray): An array of anomaly scores.

    Returns:
        float: Estimated contamination rate.
    """
    Q1 = np.percentile(scores, 25)
    Q3 = np.percentile(scores, 75)
    IQR = Q3 - Q1
    outlier_threshold = Q3 + 1.5 * IQR
    outliers = scores[scores > outlier_threshold]
    contamination = max(len(outliers) / len(scores), 0.01)  # Ensure at least 1% contamination
    
    if contamination > 0.15:
        # Limiting the contamination rate to 15% to avoid too many false positives
        contamination = 0.15
    return contamination


### Detect Univariate Anomalies

The `detect_univariate_anomalies` function applies the Isolation Forest algorithm to detect anomalies within each numeric column of the DataFrame independently. It caters to the option of excluding data points already identified as anomalies in a rule-based manner, allowing for a layered approach to anomaly detection. By assessing each column separately, this method focuses on identifying data points that are anomalous with respect to the univariate distribution of each feature. The function dynamically determines the contamination rate using the `determine_contamination` function, ensuring the anomaly detection is tailored to the specific characteristics of each dataset. Anomalies are flagged, and their details are recorded for further analysis.


In [158]:
def detect_univariate_anomalies(df, criteria_and_pvid, rule_based_anomalies, exclude_rule_based=True):
    """
    Detects univariate anomalies for each numeric column in the DataFrame using the Isolation Forest algorithm,
    optionally excluding data points already flagged as rule-based anomalies.

    Args:
        df (pd.DataFrame): DataFrame containing the data.
        criteria_and_pvid (dict): Dictionary with anomaly criteria and PVIDs for each parameter.
        rule_based_anomalies (list): List of dictionaries with details about each detected rule-based anomaly.
        exclude_rule_based (bool): If True, excludes points already flagged as rule-based anomalies.
    """
    univariate_anomalies = []

    for param, criteria in criteria_and_pvid.items():
        if param in df.columns and pd.api.types.is_numeric_dtype(df[param]):
            data_for_model = df[[param]].dropna()

            # Exclude rule-based anomalies if requested
            if exclude_rule_based:
                rule_based_anomaly_indices = [anomaly['Timestamp'] for anomaly in rule_based_anomalies if anomaly['Parameter Name'] == param]
                data_for_model = data_for_model[~data_for_model.index.isin(rule_based_anomaly_indices)]

            if data_for_model.empty:
                continue

            contamination_rate = determine_contamination(data_for_model[param])
            model = IsolationForest(contamination=contamination_rate, random_state=42)
            reshaped_data = data_for_model.values.reshape(-1, 1)
            model.fit(reshaped_data)
            scores = -model.decision_function(reshaped_data).reshape(-1)  # Negate the scores to make them positive

            # Score normalization between 0 and 100
            min_score, max_score = scores.min(), scores.max()
            scores_normalized = 100.0 * (scores - min_score) / (max_score - min_score)

            predictions = model.predict(reshaped_data)

            # Initialize all values to 0 and mark detected anomalies as 1
            df[f"{param}_Anomaly_Univariate"] = 0
            anomaly_indices = data_for_model.index[predictions == -1]
            df.loc[anomaly_indices, f"{param}_Anomaly_Univariate"] = 1  # Mark detected anomalies as 1

            for idx, score_normalized in zip(anomaly_indices, scores_normalized[predictions == -1]):
                add_anomaly_details(univariate_anomalies, param, criteria['pvid'], idx, score_normalized, 'Univariate', f'Detected as univariate anomaly with value {df.at[idx, param]}')

    return df, univariate_anomalies


<h2 align="center">Multivariate Anomaly Detection</h2>

### Optimal PCA Components

The `optimal_pca_components` function is designed to determine the optimal number of principal components needed to capture a significant portion of the variance in the data. By applying PCA (Principal Component Analysis) and calculating the cumulative sum of explained variance ratio, it identifies the smallest number of components that together explain at least a specified threshold of the total variance (default is 95%). This approach is crucial for dimensionality reduction, ensuring that the transformed data retains most of the original information while reducing the complexity of the dataset.

### Optimal KMeans Clusters

Identifying the optimal number of clusters is a key step in clustering algorithms like KMeans. The `optimal_kmeans_clusters` function evaluates different numbers of clusters (up to a specified maximum) and selects the one with the highest Silhouette score, indicating the best definition of clusters. The Silhouette score measures how similar an object is to its own cluster compared to other clusters, providing a metric to assess the separation distance between the resulting clusters. This function is essential for ensuring the effectiveness of KMeans clustering by determining the most appropriate number of clusters to use for the data.

### Calculating Anomaly Scores

The `calculate_anomaly_scores` function computes anomaly scores for each data point based on its distance from the nearest cluster center, using a trained KMeans model. These distances are then normalized to a range of 0 to 1, with higher scores indicating greater deviation from the nearest cluster center and, thus, a higher likelihood of being an anomaly. This scoring system is instrumental in quantifying the degree of anomalousness of each observation, facilitating the identification of outliers in the dataset.

### Determining Anomaly Threshold

Setting an appropriate threshold for anomaly detection is critical for distinguishing between normal and anomalous observations. The `determine_threshold` function calculates this threshold by identifying the value at a specified percentile (default is 95th percentile) of the anomaly scores distribution. Data points with scores above this threshold are considered anomalies. This method allows for a dynamic thresholding strategy that adapts to the specific anomaly score distribution of the dataset, ensuring that the threshold is both data-driven and adaptable to different contexts.


In [159]:

# Function for determining the optimal number of clusters
def optimal_pca_components(data, variance_threshold=0.95):
    pca = PCA()
    pca.fit(data)
    total_variance = np.cumsum(pca.explained_variance_ratio_)
    n_components = np.argmax(total_variance >= variance_threshold) + 1
    return n_components

def optimal_kmeans_clusters(data, max_clusters=20):
    silhouette_scores = []
    for n_clusters in range(2, max_clusters + 1):
        kmeans = KMeans(n_clusters=n_clusters, n_init=10, random_state=42) 
        kmeans.fit(data)
        score = silhouette_score(data, kmeans.labels_)
        silhouette_scores.append((n_clusters, score))
    
    # Select the best number of clusters based on the Silhouette ratings.
    n_clusters, _ = max(silhouette_scores, key=lambda x: x[1])
    return n_clusters


# Function for calculating anomaly scores
def calculate_anomaly_scores(data, kmeans_model):
    distances = [np.linalg.norm(x - kmeans_model.cluster_centers_[kmeans_model.predict([x])[0]]) for x in data]
    scaler = MinMaxScaler()
    scaled_distances = scaler.fit_transform(np.array(distances).reshape(-1, 1)).flatten()
    return scaled_distances

# Function for determining the anomaly threshold
def determine_threshold(distances, percentile=95):
    threshold = np.percentile(distances, percentile)
    return threshold

### KMeans Clustering and PCA Anaylsis

For detecting complex anomalies that span multiple features, this approach utilizes the KMeans clustering algorithm as part of the multivariate anomaly detection strategy. It involves reducing the dimensionality of the data (if necessary) and applying KMeans to identify clusters within the data. Data points that do not fit well into any cluster can be considered anomalies. This method is particularly useful for identifying anomalies that only emerge from the interaction of multiple variables, offering a holistic view of the data's normal and anomalous patterns.


In [161]:
from scipy.stats import scoreatpercentile

def detect_multivariate_anomalies(df, criteria_and_pvid, univariate_anomalies, rule_based_anomalies, anomalies_list):
    """
    Detects multivariate anomalies using PCA for dimensionality reduction, K-Means for clustering,
    and includes detailed steps for determining contamination, optimal PCA components, and cluster numbers.
    Args:
        df (pd.DataFrame): DataFrame containing the data.
        anomalies_list (list): List to which detected anomaly details will be appended.
    Returns:
        pd.DataFrame: Updated DataFrame with a new column indicating multivariate anomalies.
        list: Updated list with details about each detected multivariate anomaly.
    """
    # Exclude previously detected rule-based anomalies
    clean_df = df[df['Anomaly_Rulebased'] == 0]
    numeric_data = clean_df.select_dtypes(include=np.float64)
      
    # Standardize the data
    scaler = StandardScaler()
    scaled_data = scaler.fit_transform(numeric_data)

    # Determine optimal PCA components
    n_components = optimal_pca_components(scaled_data)
    pca = PCA(n_components=n_components)
    pca_data = pca.fit_transform(scaled_data)

    # Determine optimal K-Means clusters
    n_clusters = optimal_kmeans_clusters(pca_data)
    kmeans = KMeans(n_clusters=n_clusters, random_state=42)
    kmeans.fit(pca_data)

    # Calculate anomaly scores
    distances = kmeans.transform(pca_data).min(axis=1)
    scores = -distances  # Negate the distances to align with the Isolation Forest convention
    
    # Normalize scores to a 0-100 scale
    min_score, max_score = scores.min(), scores.max()
    scores_normalized = 100.0 * (scores - min_score) / (max_score - min_score)

    # Determine threshold using the contamination rate
    contamination_rate = determine_contamination(scores)
    threshold = scoreatpercentile(scores, 100 * contamination_rate)

    # Mark anomalies based on the threshold
    df['Anomaly_Multivariate'] = 0  # Initialize the column
    anomaly_indices = clean_df.index[scores > threshold]
    df.loc[anomaly_indices, 'Anomaly_Multivariate'] = 1
    univariate_timestamps = set(anomaly['Timestamp'] for anomaly in univariate_anomalies)
    
    multivariate_list = []
    # Add details of detected anomalies to the list
    for idx in anomaly_indices:
        if idx not in univariate_timestamps:
            for col in numeric_data.columns:
                normalized_score = scores_normalized[clean_df.index == idx][0]
                pvid = criteria_and_pvid[col]['pvid'] if col in criteria_and_pvid else 'N/A'
                add_anomaly_details(multivariate_list, col, pvid, idx, normalized_score, 'Multivariate', 'Detected through KMeans')

    return df, multivariate_list


### Multivariate Anomaly Detection with DBSCAN

As an alternative to the KMeans clustering approach, DBSCAN (Density-Based Spatial Clustering of Applications with Noise) offers a powerful method for multivariate anomaly detection. DBSCAN does not require pre-specification of the number of clusters, unlike KMeans. It works by identifying dense clusters of observations and treating points that do not belong to any cluster as anomalies. This characteristic makes DBSCAN particularly useful for datasets with complex structures or where the density of data points varies significantly. Anomalies detected through DBSCAN are considered outliers based on their spatial isolation from denser regions, providing a different perspective on what constitutes an anomaly.


In [178]:
from sklearn.cluster import DBSCAN
from sklearn.preprocessing import StandardScaler



def ddetect_multivariate_anomalies_dbscan(df, criteria_and_pvid, univariate_anomalies, rule_based_anomalies, eps=0.5, min_samples=5):
    """
    Detects multivariate anomalies using DBSCAN, excluding rule-based anomalies but including univariate anomalies in the analysis.
    Afterwards, it excludes anomalies that were already identified as univariate from the list of detected multivariate anomalies.
    
    Args:
        df (pd.DataFrame): DataFrame containing the data.
        criteria_and_pvid (dict): Dictionary containing anomaly criteria and PVIDs for each parameter.
        univariate_anomalies (list): List of dictionaries, each containing details of a univariate anomaly.
        rule_based_anomalies (list): List of dictionaries, each containing details of a rule-based anomaly.
        eps (float): The maximum distance between two samples for them to be considered as in the same neighborhood.
        min_samples (int): The number of samples in a neighborhood for a point to be considered as a core point.
        
    Returns:
        pd.DataFrame: DataFrame with an additional column indicating multivariate anomalies.
        list: Updated list of multivariate anomalies, excluding those identified by univariate analysis.
    """
        # Exclude previously detected rule-based anomalies
    clean_df = df[df['Anomaly_Rulebased'] == 0]
    numeric_data = clean_df.select_dtypes(include=np.float64)
      
    # Standardize the data
    scaler = StandardScaler()
    data_scaled = scaler.fit_transform(numeric_data)

    # Applying DBSCAN
    dbscan = DBSCAN(eps=eps, min_samples=min_samples)
    clusters = dbscan.fit_predict(data_scaled)

    # Marking DBSCAN-detected anomalies
    df['Anomaly_Multivariate'] = 0
    clean_df_indices = clean_df.index[clusters == -1]
    df.loc[clean_df_indices, 'Anomaly_Multivariate'] = 1

    # Preparing the list of multivariate anomalies, excluding univariate anomalies
    univariate_timestamps = set(anomaly['Timestamp'] for anomaly in univariate_anomalies)
    multivariate_anomalies = []

    for idx in clean_df_indices:
        if idx not in univariate_timestamps:
            for col in numeric_data.columns:
                pvid = criteria_and_pvid[col]['pvid'] if col in criteria_and_pvid else 'N/A'
                add_anomaly_details(multivariate_anomalies, col, pvid, idx, 'N/A', 'Multivariate', 'Detected through DBSCAN')

    return df, multivariate_anomalies



## Saving Anomalies

Once anomalies have been detected using rule-based, univariate, multivariate (KMeans or DBSCAN) methods, it is crucial to save these findings for further analysis or reporting. The process involves recording the details of each anomaly, such as the timestamp, variable name, anomaly score, and type of detection method used. This information can be saved in a structured format like CSV or directly into a database, depending on the workflow and requirements. Saving anomalies systematically facilitates tracking, reviewing, and acting upon anomalous events identified in the data.


In [179]:

def save_anomalies_to_csv(anomalies_list, file_name="anomalies_detected.csv"):
    """
    Saves the details of detected anomalies to a CSV file.

    Args:
        anomalies_list (list): A list of dictionaries, each containing details of an anomaly.
        file_name (str): The name of the CSV file to which the anomalies will be saved.
    """
    # Convert the list of anomalies to a DataFrame
    anomalies_df = pd.DataFrame(anomalies_list)
    
    # Save the DataFrame to a CSV file
    anomalies_df.to_csv(file_name, index=False, sep=';', decimal=',', encoding='utf-8')
    
    print(f"Anomalies have been saved to {file_name}.")

## Running the Code

This project offers two primary pathways for anomaly detection based on the source of input data: CSV files and direct database queries. For CSV-based workflows, data is loaded from CSV files, processed, and the detected anomalies are saved back to CSV files. Alternatively, for database-centric workflows, data is queried directly from a database, processed for anomaly detection, and the results can be saved back to the database or another designated storage. This flexibility allows users to integrate anomaly detection seamlessly into various data management ecosystems, catering to different operational requirements and data accessibility scenarios.


In [251]:
# Load the data: 
# 1- from CSV file

# 2- from SQL server
df = load_data_from_db(sql_query, conn_str, timestamp_col, datetime_format)

# Handling missing data
df = handle_missing_values(df)

# Reading anomaly criteria and PVID information
criteria_and_pvid = read_anomaly_criteria_and_pvid('Descriptions.xlsx')

In [252]:

# Rule-based anomaly detection
df, rule_based_anomalies = detect_rule_based_anomalies(df, criteria_and_pvid)

# Univariate anomaly detection
df, univariate_anomalies = detect_univariate_anomalies(df, criteria_and_pvid, rule_based_anomalies, exclude_rule_based=True)

# Multivariate anomaly detection
# 1- KMeans
#df, multivariate_anomalies = detect_multivariate_anomalies(df, criteria_and_pvid, univariate_anomalies, rule_based_anomalies)
# 2-DBSCAN
df, multivariate_anomalies = detect_multivariate_anomalies_dbscan(df, criteria_and_pvid, univariate_anomalies, rule_based_anomalies, eps=0.5, min_samples=5)

In [255]:
# Saving anomalies to CSV
combined_anomalies = rule_based_anomalies + univariate_anomalies + multivariate_anomalies
save_anomalies_to_csv(combined_anomalies, "anomalies_detected.csv")

Anomalies have been saved to anomalies_detected.csv.




## Visualizing the Data and Anomalies

Visualization plays a crucial role in data analysis, providing intuitive insights into the underlying patterns and anomalies within the dataset. In this section, we employ various plotting techniques to illustrate the distribution of data points and highlight detected anomalies. By visualizing the data, we can easily communicate complex insights, identify trends, and showcase the effectiveness of our anomaly detection algorithms. Plots such as time series graphs, scatter plots, and histograms will be used to display both normal and anomalous data points in different contexts.

### Time Series Plots

Time series plots are particularly useful for visualizing the behavior of variables over time. For detected anomalies, highlighting them on a time series plot can help identify when unusual patterns occur and how they deviate from normal trends. This visualization is essential for time-dependent datasets, where understanding the temporal context of anomalies can provide critical insights into potential issues or events that caused the anomalies.

### Scatter Plots for Anomaly Detection

Scatter plots offer a straightforward way to visualize the relationship between two variables and identify outliers. By plotting detected anomalies with a different marker or color, we can discern their distribution and isolation from normal data points. This method is highly effective in multivariate anomaly detection, where the interaction between variables is key to identifying anomalous behavior.



In [264]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

def plot_anomalies_interactive(df, criteria_and_pvid, anomalies_list, show_univariate=True, show_multivariate=True):
    """
    Plot anomalies for each variable in 'criteria' using Plotly's go.Scatter. 
    """
    fig = make_subplots(rows=len(criteria_and_pvid), cols=1, shared_xaxes=False, subplot_titles=list(criteria_and_pvid.keys()))

    legend_shown = {"Rule-based": False, "Univariate": False, "Multivariate": False}

    row = 1
    for param, criteria in criteria_and_pvid.items():
        if param in df.columns:
            fig.add_trace(go.Scatter(x=df.index, y=df[param], mode='lines', name='Values', showlegend=False), row=row, col=1)
            lower_bound, upper_bound = criteria['min'], criteria['max']
            fig.add_hline(y=lower_bound, line_dash="dash", line_color="green", row=row, col=1, showlegend=False)
            fig.add_hline(y=upper_bound, line_dash="dash", line_color="green", row=row, col=1, showlegend=False)
            
            for anomaly_type in ['Rule-based', 'Univariate', 'Multivariate']:
                if anomaly_type == 'Univariate' and not show_univariate:
                    continue
                if anomaly_type == 'Multivariate' and not show_multivariate:
                    continue
                
                anomaly_indices = [anomaly['Timestamp'] for anomaly in anomalies_list if anomaly['Parameter Name'] == param and anomaly['Anomaly Type'] == anomaly_type]
                if anomaly_indices:
                    color = {'Rule-based': 'red', 'Univariate': 'orange', 'Multivariate': 'purple'}[anomaly_type]
                    show_legend = not legend_shown[anomaly_type]
                    fig.add_trace(go.Scatter(x=anomaly_indices, y=df.loc[anomaly_indices, param], mode='markers', marker=dict(color=color), name=anomaly_type, showlegend=show_legend), row=row, col=1)
                    legend_shown[anomaly_type] = True
            
            row += 1

    # Move legend to bottom of the plot to avoid overlapping
    fig.update_layout(height=400*len(criteria_and_pvid), title='Anomalies Overview', showlegend=True,
                      legend=dict(orientation="h", yanchor="bottom", y=1.1, xanchor="center", x=0.5))

    fig.show(config={"doubleClick": "reset"})

In [265]:
plot_anomalies_interactive(df, criteria_and_pvid, combined_anomalies, show_univariate=True, show_multivariate=True)

In [ ]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def plot_multivariate_anomalies_individually(df, anomalies_list, criteria):
    """
    Plot multivariate anomalies for each variable in 'criteria' using Plotly's go.Scatter.
    
    Args:
        df (DataFrame): The DataFrame containing the data.
        anomalies_list (list): List containing details of all detected anomalies, 
                               each anomaly is a dict with 'Timestamp' and 'Anomaly Type'.
        criteria (list): List of column names to be plotted individually.
    """
    # Filter to get timestamps of multivariate anomalies
    multivariate_timestamps = [anomaly['Timestamp'] for anomaly in anomalies_list if anomaly['Anomaly Type'] == 'Multivariate']

    # Create a subplot for each variable in criteria
    criteria = list(criteria)
    rows = len(criteria)
    fig = make_subplots(rows=rows, cols=1, subplot_titles=criteria)

    for i, variable in enumerate(criteria, start=1):
        # Plot each variable from criteria
        fig.add_trace(go.Scatter(x=df.index, y=df[variable], mode='lines', name=variable), row=i, col=1)
        
        # Add anomalies for this variable
        anomaly_values = [df.loc[idx][variable] for idx in multivariate_timestamps if idx in df.index]
        fig.add_trace(go.Scatter(x=multivariate_timestamps, y=anomaly_values, mode='markers', name='Anomalies', marker=dict(color='green', size=10)), row=i, col=1)

    fig.update_layout(height=300*rows, title_text="Multivariate Anomalies for Selected Variables", showlegend=False)
    fig.show()



In [ ]:
plot_multivariate_anomalies_individually(df, multivariate_anomalies, criteria_and_pvid.keys())

## Conclusion

This project demonstrates a comprehensive approach to anomaly detection, incorporating both univariate and multivariate methods, including rule-based detection, KMeans, and DBSCAN for more complex data relationships. Through careful preprocessing, including handling missing values and leveraging external criteria for anomalies, we've prepared our dataset for effective analysis. Visualization techniques further allowed us to explore and present our findings, revealing the nuanced nature of anomalies in time-series data. Moving forward, these insights can be used to improve operational efficiency, detect fraudulent activity, or identify opportunities for further investigation. The flexibility of our approach ensures that it can be adapted to various datasets and anomaly detection scenarios, providing a robust foundation for future data analysis projects.
